In [ ]:
# default_exp pytwitter

# Twitter sentiment with tweepy and vader

> Using tweepy to get twitter data, and do some sentiment analysis

In [ ]:
#hide
from nbdev.showdoc import *

In [ ]:
# set chdir to current dir
import os
import sys
import json
import sqlite3
import string
import pickle
import itertools
import pandas as pd
import regex as re
import time
# sys.path.insert(0, os.path.realpath(os.path.dirname(__file__)))
# os.chdir(os.path.realpath(os.path.dirname(__file__)))

from unidecode import unidecode
from threading import Lock, Timer
from collections import Counter
from tweepy import Stream, API
from tweepy import OAuthHandler
from tweepy.streaming import StreamListener

from textblob import TextBlob
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer

In [ ]:
from pyexplore.stopwords import stop_words

In [ ]:
#hide
# Twitter consumer key, consumer secret, access token, access secret.
ckey="uD5be2saN7fQZSaQ9OY9Y5w0C"
csecret="vqWDPLGAx5MoNe8ELlocJ2zfARgnetIFoJXlsSH1ACBrRZjMef"
atoken="86935267-XH1dJF8RQQ5wDNtkGt5RHcrEivGaHcGGflLtVdZFL"
asecret="ZPawPJA7WG9FZHPXrTLHTpXV6oJIW4tr9BseWohEP8NQo"

In [ ]:
analyzer = SentimentIntensityAnalyzer()
# isolation lever disables automatic transactions,
# we are disabling thread check as we are creating connection here, but we'll be inserting from a separate thread (no need for serialization)
conn = sqlite3.connect('twitter.db', isolation_level=None, check_same_thread=False)
c = conn.cursor()

def create_table():
    try:

        # http://www.sqlite.org/pragma.html#pragma_journal_mode
        # for us - it allows concurrent write and reads
        c.execute("PRAGMA journal_mode=wal")
        c.execute("PRAGMA wal_checkpoint=TRUNCATE")
        #c.execute("PRAGMA journal_mode=PERSIST")

        # changed unix to INTEGER (it is integer, sqlite can use up to 8-byte long integers)
        c.execute("CREATE TABLE IF NOT EXISTS sentiment(id INTEGER PRIMARY KEY AUTOINCREMENT, unix INTEGER, tweet TEXT, sentiment REAL)")
        # key-value table for random stuff
        c.execute("CREATE TABLE IF NOT EXISTS misc(key TEXT PRIMARY KEY, value TEXT)")
        # id on index, both as DESC (as you are sorting in DESC order)
        c.execute("CREATE INDEX id_unix ON sentiment (id DESC, unix DESC)")
        # out full-text search table, i choosed creating data from external (content) table - sentiment
        # instead of directly inserting to that table, as we are saving more data than just text
        # https://sqlite.org/fts5.html - 4.4.2
        c.execute("CREATE VIRTUAL TABLE sentiment_fts USING fts5(tweet, content=sentiment, content_rowid=id, prefix=1, prefix=2, prefix=3)")
        # that trigger will automagically update out table when row is interted
        # (requires additional triggers on update and delete)
        c.execute("""
            CREATE TRIGGER sentiment_insert AFTER INSERT ON sentiment BEGIN
                INSERT INTO sentiment_fts(rowid, tweet) VALUES (new.id, new.tweet);
            END
        """)
    except Exception as e:
        print(str(e))
create_table()

# create lock
lock = Lock()

class listener(StreamListener):

    data = []
    lock = None

    def __init__(self, lock):

        # create lock
        self.lock = lock

        # init timer for database save
        self.save_in_database()

        # call __inint__ of super class
        super().__init__()

    def save_in_database(self):

        # set a timer (1 second)
        Timer(1, self.save_in_database).start()

        # with lock, if there's data, save in transaction using one bulk query
        with self.lock:
            if len(self.data):
                c.execute('BEGIN TRANSACTION')
                try:
                    c.executemany("INSERT INTO sentiment (unix, tweet, sentiment) VALUES (?, ?, ?)", self.data)
                except:
                    pass
                c.execute('COMMIT')

                self.data = []

    def on_data(self, data):
        try:
            #print('data')
            data = json.loads(data)
            # there are records like that:
            # {'limit': {'track': 14667, 'timestamp_ms': '1520216832822'}}
            if 'truncated' not in data:
                #print(data)
                return True
            if data['truncated']:
                tweet = unidecode(data['extended_tweet']['full_text'])
            else:
                tweet = unidecode(data['text'])
            time_ms = data['timestamp_ms']
            vs = analyzer.polarity_scores(tweet)
            sentiment = vs['compound']
            #print(time_ms, tweet, sentiment)

            # append to data list (to be saved every 1 second)
            with self.lock:
                self.data.append((time_ms, tweet, sentiment))

        except KeyError as e:
            #print(data)
            print(str(e))
        return True

    def on_error(self, status):
        print(status)


# make a counter with blacklist words and empty word with some big value - we'll use it later to filter counter
stop_words.append('')
blacklist_counter = Counter(dict(zip(stop_words, [1000000] * len(stop_words))))

# complie a regex for split operations (punctuation list, plus space and new line)
punctuation = [str(i) for i in string.punctuation]
split_regex = re.compile("[ \n" + re.escape("".join(punctuation)) + ']')

def map_nouns(col):
    return [word[0] for word in TextBlob(col).tags if word[1] == u'NNP']

# generate "trending"
def generate_trending():

    try:
        # select last 10k tweets
        df = pd.read_sql("SELECT * FROM sentiment ORDER BY id DESC, unix DESC LIMIT 10000", conn)
        df['nouns'] = list(map(map_nouns,df['tweet']))

        # make tokens
        tokens = split_regex.split(' '.join(list(itertools.chain.from_iterable(df['nouns'].values.tolist()))).lower())
        # clean and get top 10
        trending = (Counter(tokens) - blacklist_counter).most_common(10)

        # get sentiments
        trending_with_sentiment = {}
        for term, count in trending:
            df = pd.read_sql("SELECT sentiment.* FROM  sentiment_fts fts LEFT JOIN sentiment ON fts.rowid = sentiment.id WHERE fts.sentiment_fts MATCH ? ORDER BY fts.rowid DESC LIMIT 1000", conn, params=(term,))
            trending_with_sentiment[term] = [df['sentiment'].mean(), count]

        # save in a database
        with lock:
            c.execute('BEGIN TRANSACTION')
            try:
                c.execute("REPLACE INTO misc (key, value) VALUES ('trending', ?)", (pickle.dumps(trending_with_sentiment),))
            except:
                pass
            c.execute('COMMIT')


    except Exception as e:
        with open('errors.txt','a') as f:
            f.write(str(e))
            f.write('\n')
    finally:
        Timer(5, generate_trending).start()

In [ ]:
Timer(1, generate_trending).start()

while True:

    try:
        auth = OAuthHandler(ckey, csecret)
        auth.set_access_token(atoken, asecret)
        twitterStream = Stream(auth, listener(lock))
        twitterStream.filter(track=["a","e","i","o","u"])
    except Exception as e:
        print(str(e))
        time.sleep(5)


In [ ]:
import tweepy
auth = tweepy.OAuthHandler(ckey, csecret)
auth.set_access_token(atoken, asecret)

# api = tweepy.API(auth)
# public_tweets = api.home_timeline()
# for tweet in public_tweets:
#     print(tweet.text)

In [ ]:
class MyStreamListener(tweepy.StreamListener):
    def on_status(self, status):
        print(status.text)

In [ ]:
keywords = ['transport','transit','car','bus','train','tram','rail','metro','motor','bicyle',
            'travel','commute','flight','run','jog','walk','cycle','cycling','scoot',
            'taxi','MaaS','Uber','Lyft','Ola','Didi','Gojek','Snap','Grab','Via','Cab','Catch','Scooti','HOP']
# aus_loc = [113.338953078, -43.6345972634, 153.569469029, -10.6681857235]

In [ ]:
not_enough = True
count = 0
N = 20
while not_enough:
    try:
        stream = tweepy.Stream(auth, listener=MyStreamListener())
        stream.filter(track=keywords)
        count += 1
        if count == N: not_enough = False
    except:
        break

Check out what I just added to my closet on Poshmark: NWT! LAST ONE! New Wide Brim Straw Cowboy Hat.… https://t.co/jQk5V8DCDQ
RT @TrainingMindful: “You gotta train your mind to be stronger than your emotions, or else you’ll lose yourself every time.”
RT @SuzanneEvans1: Is there a greater hypocrite on air? https://t.co/zDOBOr9bBy
RT @Diablo: Huge congrats to meatr0o, Heckson, and Whisperra on that World Record New Game co-op run in Diablo III during @GamesDoneQuick!…
RT @jiggyjayy2: If she wanna forgive her abuser that's the cycle of abuse, it happens. But the ShadeRoom don't need to glorify abusive rela…
RT @HawleyMO: Tonight while I was in Missouri, Antifa scumbags came to our place in DC and threatened my wife and newborn daughter, who can…
RT @PuDiYaaa: Living in times of Hindu Rashtra

Via IG! https://t.co/hQjcp5oOuO
RT @saint_prems: affordable pr3miums ahead! dm to avaaaail 🙈

  ━  giftcode method/PH BASED
  ━  guaranteed no hold/wipe
  ━  full warranty…
RT @mumbaimatterz: Thanks 

RT @robocosan: 🐻ゲリラ配信🐻
枠ﾊﾞｸﾞにつき移動しました＞＜
NEW MY CAR に乗ってGO DRIVEだああああああ！！
苦手なコントローラーをここから。。。目指せ上達！

⏰１６時～開始！！
【マリオカート8DX】新しい車でGOGO!!コントローラーと…
@TongueRust goodnye scoot
RT @_MyLumin: Voice technologies using #AI are being used to help combat loneliness. Should they be used more widely as coronavirus spreads…
RT @ingasiania: Imagine this happening at Afya Center and it’s your first time in Nairobi from Kakamega
RT @Univers_Bangtan: 📸 Prévia de fotos do Run BTS! - Episódio 123 (2/2)

• Hyung Line 

🐳 @BTS_twt https://t.co/WiWakDiDT6
RT @Vantedxboy: [📸] Imágenes previas del Run BTS!  — Episodio 123 🍴

@BTS_twt ( 1 / 2) https://t.co/fVOqwlwVyx
RT @pissaround: my kids gonna catch me at their house parties if I keep missing out on my 20s like this
RT @charts_k: .@BTS_twt's "BE" rises to #21 (+5) on the Billboard 200 in its 6th week with 23k units sold (via chartdata). *Peak: #1*
thank you .
RT @ProtecDes: Un monde en plastique (2/4) : Au plastique, le design reconnaissant via @franceculture ht

Since I knew that rice can be cooked like this https://t.co/HYjbSg0nxm via @YouTube
RT @TomFitton: Communists threaten wife and baby of US Senator. Where were DC police?
RT @DJStutz_: Why isn’t car insurance discounted, weh we ah go?
RT @EChabriere: BMPM/IHU quand l'excellence rencontre l'excellence 

Debriefing du Contre-amiral Patrick Augier, commandant des Marins Pomp…
Gordon helps Magic beat Cavaliers 103-83, snap 2-game skid https://t.co/Tu3WXTtaMP
RT @clambuoyance: [#TALESFROMTHEDREAMSMP rp] 

(1/2) The Village That Went Mad
aka Karl does some time shenanigans!

pls click thread for p…
RT @alptraumco: NOW DOING CAR DECALS! message for colors and or customs 💙 https://t.co/OTPZrfTxL4
RT @michelledonelan: University students on critical courses such as medicine and healthcare will still receive face-to-face education and…
Get it free: Free: Robinhood Stock Trading + 1 Free Share of Stock  https://t.co/RXUk4tLBGD via @StackSocial
RT @manukumarjain: #Mi10i powered by @Qualcomm #Snapdr

RT @belovedjake: pov : try to catch sunghoon if you can https://t.co/kL7mtyhIX2
RT @kalidevi: .@DrewSpringer "...if you don’t want to be described as scum...maybe you shouldn’t run for political office.”@AngelaGreben ".…
RT @Hiphop__convo: Best hip hop discog and that’s a fact
Ayo too cute its a madness
RT @marco_gervasoni: New Covid variant will increase stress on global economy and widen inequality via @FT
 https://t.co/D82Ownqb6K
RT @SrimantiG: In Oct 2018, the state govt. refused to cooperate with the CAG in an audit of Kanyashree Prakalpa. What prompted the state g…
K/DA - POP/STARS  | (여자) 아이들 Version https://t.co/nVtLuTeTVL via @YouTube 

pcd pcd pcd
RT @SKIANSArmy: EXCLUSIVE 🏆:

Promo Cut Of Our SK In COOK WITH COMALI Show Via 'VIJAY TV' To Be Telecasted On 9th &amp; 10th January..!🎉😍

#DOC…
Prove it. Where’s the evidence? No one trusts MAGAts because all you do is lie. So until you can prove this, you ar… https://t.co/k4XDeoLgsj
RT @NajihahAm: FREE POSTAGE ‼️ FREE POSTAGE ‼️Fr

@AusBT Useless &amp; very unhelpful statement from Cth Govt. Tell us whether vaccination will allow travel to &amp; from Au… https://t.co/La2WBVq8ta
RT @shuvenduchakr14: Over 125 BJP workers have been massacred in Bengal at d instigation of @mamataofficial in order 2 further her politica…
RT @KarenMarijeni: Annalise could walk in the courtroom drunk and win the case
RT @Toluulope: As we got to Dubai, just after immigration cleared us, they conducted covid test, there at the airport for free and they sen…
Check out what I just added to my closet on Poshmark: New! Natural Chrome Diopside Sterling Silver Ring.… https://t.co/XERQdWCkha
The atmosphere is overheated, hah! Catch me on fire, hah! The real has appeared, nanana~
RT @EatingInCommon: I have been actively participating in mutual aid for years and helping others do the same. 

I can help you, I can walk…
RT @TanaGaneva: When I worked at Whole Foods every night they made us dump EVERY leftover piece of prepared food in a trash can wi

...

RT @foton2012: #5ocaktasokaktayız diye bir tag açılmış
Tüm dostlarımıza uyarımdır .
Sakın ola uymayın katılmayın karışmayın
Polis ve halkı…
RT @hannaherss: Is your bun ever so high you have to lower your car seat
RT @_zimkhitha_: 🐰🐰 https://t.co/TZnUfcH83z
@waynegadgett Hai guys, mana" yang nak dapatkan iphone murah, berkualiti n trusted seller korang boleh follow ig… https://t.co/J8AWe8Tzrd
CONDIVIDO SONO 🤡 RENZI AMA LA POLTRONA NO 🇮🇹🇮🇹🇮🇹🇮🇹🇮🇹🇮🇹🇮🇹🇮🇹🇮🇹
RT @Paytm: Looking for 'Take a Flight' card for your #Paytm2021Wishlist? 😀

1. Follow @Paytm 
2. RT this post 🔃

Number of RTs = Number of…
RT @DanRather: Please, please, wake up America. There is a vaccine coming, but there is a lot of death and danger between now and then. Do…
@bharathbunny27 @PranitaRavi @Uber @Uber_Support @Olacabs Uber also introduced this service. OUr ride starts only after entering OTP
RT @DGTes: Cortada Carretera #M601 de Acceso al Puerto de Navacerrada en kilómetro 12,500 #Cercedilla
RT @NEOMAbs: 🤩  #NEOMAbs est 

RT @daperfectDP: Ananya Panday via-Instagram 

happiest birthday my Deepu! The warmest, loveliest, most genuine, empathetic person I know!…
RT @CodeMonkeyZ: Trump is threatening to drop all the blackmail via declassification so they dont mess with him in Congress this week.
Perh…
RT @RepBoebert: According to Speaker Pelosi, healthy Americans must wear masks, close their small businesses, and stay home at all times.…
RT @peekaymila: Let the world know that our parents in Plateau state were shot at, attacked, brutalised and arrested on Monday, January 4,…
RT @mspaintbox: twitter especially is an app that’s, just because of the way it’s built, is really not healthy most of the time. the 24/7 b…
Highkey wanna wrap my car some outrageous color.
#TheDayUwajeUp
#MotivationalQuotes 
#Facts
If you Want to be a Successful Person?
Run from the Comfort Zones!
Suffe… https://t.co/My4P1hwdRU
RT @daperfectDP: Ananya Panday via-Instagram 

happiest birthday my Deepu! The warmest, loveliest, most genui

RT @ArjunsinghWB: Didi @MamataOfficial is terrified because people are ready to respond &amp; bring down corruption, misgovernance, oppression…
RT @XiaomiIndia: 1️⃣0️⃣ #Mi10i devices to be won by answering this simple question.

Participate and RT with #ThePerfect10 and #Mi10i walk…
Dr. Anthony Fauci gave an interview to Newsweek recently, and in that interview, he hinted that there could be vacc… https://t.co/YCg6KObeQQ
＼一年の始まりはスズキのお店へ／

初売り開催日をWEBで検索し、
@suzukicojpをフォロー＆ツイートでおみくじのチャンス！

大吉で2021名様に2021円分、
中吉で10000名様に300円分の
デジタルお年玉が当たる… https://t.co/SxYlbbSanp
@marklevinshow @ELF1955 Wow! She was “that little girl on the bus” dealing with segregation caused by #CheaterBiden… https://t.co/YYBdTA1pBg
RT @leys_ash: [Behind Cut] Run BTS! - Ep.123 Preview Photos📸

@BTS_twt #방탄소년단 #BTS https://t.co/e6E0CmhASY
RT @vibizmediacom: Menjelang Rally Besar-besaran dan Penolakan Pemilu di Kongres Amerika: 6 Januari 2021 https://t.co/GWx7uorHWY via @vibiz…
RT @NerdingAtWork: @NaNawrote I just want a p

RT @sisterariola: “yes i run my own business”

the business in question: https://t.co/3XmQuvuvxA
RT @vtc_crash: #Taxienlucha #mejorentaxi #quejasvtc #eltaxiunido #eligetaxi
Video del accidente de la vtc en la Avda de Andalucía con Gran…
RT @ProudSocialist: There is nobody more out of touch on planet earth than the American ruling class.
RT @glayzinho: amiga, o preço do uber 😭😭😭 https://t.co/840ImQPnSs
@ruthzieIlerelah Run for your life
Another pandemic record: TSA screened 1.3 million travelers Sunday as holiday travelers headed home… https://t.co/0QQFyoM5OO
RT @faiththegemini: when im on the aux , i play music for me 😂 fuck the rest of yall in the car
RT @cnnbrk: Los Angeles County EMS tells ambulance crews not to transport patients with little chance of survival to hospitals and conserve…
RT @hlulani_com: First journal paper is out: 

Identifying transport policy gaps in student travel demand management in South Africa

@Reha…
RT @hourlyjeno: #제노 #NCTDREAM © catch me if you can https

@anyothersky don't let the gamer bros who make hating the other faction their entire personality catch you saying that, they'll post at you
RT @JamesOKeefeIII: If you’re in Georgia tomorrow and see anything suspicious you can contact us @Project_Veritas via DM or email us at ver…
On est foutus allez hop rideau c'est terminé merci pour tout mais on mérite on est trop cons.
RT @LeClivia: @mandiiuwu @UnemploymentPUA @AshMobleyW @MrMcDubDub @AlwaysOverIt1 @Natasha07174717 @Lynnblue19 @mercedessnitzel @LoganOUT1 @…
RT @KevinSvenson_: I would argue that this is the biggest news of the year for the #Crypto Industry. This legitimizes #Bitcoin &amp; #Ethereum…
RT @catturd2: Kamala Tells Tall Tale of How She Fell Out of a Stroller During Civil Rights March, Then Told Her Mom All She Wanted Was "Fwe…
RT @Pervaizistan: NEW: The LA County EMS has directed ambulance crews not to transport patients with little chance of survival to hospitals…
RT @LilGothMermaid: I had four doctors appointments to dea